In [1]:
#Detecting Labels,logo
import argparse
import io
import os
import pandas as pd
import types
import numpy as np
import time
from google.cloud import vision
from google.oauth2 import service_account

# Image labels detection

In [2]:
def detect_labels_image(images_path, creds_path):
    """Detects labels in the file."""
    credentials = service_account.Credentials.from_service_account_file(creds_path)
    scoped_credentials = credentials.with_scopes(
        ['https://www.googleapis.com/auth/cloud-platform'])
    client = vision.ImageAnnotatorClient(credentials=credentials)
    #input the maximum
    max=6
    filenames = [filename for filename in os.listdir(images_path) if 'DS_Store' not in filename]    
    index=0
    ind=0
    ite_num=len(filenames)//max
    structured=[]
    for ite in range(ite_num+1):
        if ite!=ite_num:
            file_name=[file for file in filenames[index:index+max]]
            index=index+max
        else: 
            file_name=[file for file in filenames[max*ite_num:]]
        
        
        requests = []
        for filename in file_name: 
            with io.open(images_path+filename, 'rb') as image_file:
                content = image_file.read()
                requests.append({
                    "image":{"content":content},
                    "features":[
                        {"type":"LABEL_DETECTION"}
                    ]})
        resp = client.batch_annotate_images(requests)
        response = resp.responses
        for num in range(len(response)):
            label=response[num].label_annotations
            for la in label:
                structured.append([filenames[ind],la.description,la.score])
            ind+=1


    return structured

# Image faces detection

In [652]:
def detect_faces_image(images_path, creds_path):
    """Detects labels in the file."""
    credentials = service_account.Credentials.from_service_account_file(creds_path)
    scoped_credentials = credentials.with_scopes(
        ['https://www.googleapis.com/auth/cloud-platform'])
    client = vision.ImageAnnotatorClient(credentials=credentials)
    #input the maximum
    max=6
    filenames = [filename for filename in os.listdir(images_path) if 'DS_Store' not in filename]    
    index=0
    ind=0
    id=0
    ite_num=len(filenames)//max
    structured=[]
    for ite in range(ite_num+1):
        if ite!=ite_num:
            file_name=[file for file in filenames[index:index+max]]
            index=index+max
        else: 
            file_name=[file for file in filenames[max*ite_num:]]
        
        
        requests = []
        for filename in file_name: 
            with io.open(images_path+filename, 'rb') as image_file:
                content = image_file.read()
                requests.append({
                    "image":{"content":content},
                    "features":[
                        {"type":"FACE_DETECTION"}
                    ]})
        resp = client.batch_annotate_images(requests)
        response = resp.responses
        
        for i in range(len(response)):
            if not response[i].face_annotations:
                structured.append([filenames[ind],0])
                ind+=1
            else:
                re=response[i].face_annotations
                count=0
                for l in re:
                    count+=1
                structured.append([filenames[ind],count])
                ind+=1
               
    return(structured)



In [651]:
start_time = time.time()
stories_image=detect_faces_image('/Users/gary.zhou/Desktop/test/Stories_images/','/Users/gary.zhou/Documents/cloud_vision/service_account.json')
print("--- %s seconds ---" % (time.time() - start_time))

--- 450.16543889045715 seconds ---


In [653]:
start_time = time.time()
In_feed_image=detect_faces_image('/Users/gary.zhou/Desktop/test/In_feed_images/','/Users/gary.zhou/Documents/cloud_vision/service_account.json')
print("--- %s seconds ---" % (time.time() - start_time))

--- 785.5318791866302 seconds ---


In [654]:
df_stories_image=pd.DataFrame(stories_image,columns=['filename','count'])
df_stories_image['source']='Stories'
df_stories_image['file type']='image'

In [655]:
df_In_feed_image=pd.DataFrame(In_feed_image,columns=['filename','count'])
df_In_feed_image['source']='In_feed'
df_In_feed_image['file type']='image'

# Video labels detection

In [4]:
def detect_labels_video(images_path, creds_path):
    credentials = service_account.Credentials.from_service_account_file(creds_path)
    scoped_credentials = credentials.with_scopes(['https://www.googleapis.com/auth/cloud-platform'])
    client = vision.ImageAnnotatorClient(credentials=credentials)
    
    image_name=[filename for filename in os.listdir(images_path) if filename.endswith('.jpg')]
    video_name=[filename for filename in os.listdir(images_path) if filename.endswith('.mp4')]
    
    filenames =image_name   
    max=8
    id=0
    ind=0
    index=0
    ind=0
    video_index=0
    ite_num=len(filenames)//max
    structured=[]
    
    for ite in range(ite_num+1):
        if ite!=ite_num:
            file_name=[file for file in filenames[index:index+max]]
            index=index+max
        else: 
            file_name=[file for file in filenames[max*ite_num:]]

        requests=[]
        for filename in file_name: 
            with io.open(images_path+filename, 'rb') as image_file:
                content = image_file.read()
                requests.append({
                    "image":{"content":content},
                    "features":[
                        {"type":"LABEL_DETECTION"}
                    ]})
        resp = client.batch_annotate_images(requests)
        response = resp.responses
        
        for i in range(len(response)):
            if image_name[ind][:-8]!=video_name[video_index]:
                video_index+=1
            label=response[i].label_annotations
            id=id+1
            for la in label:
                structured.append([video_index,video_name[video_index],la.description,la.score])
            ind+=1
                

                
    #combine group images to single row           
    df_image=pd.DataFrame(structured,columns=['video_index','filename','object','probability'])
    return(df_image)    
    

In [749]:
dftest=detect_labels_video('/Users/gary.zhou/Desktop/test/test/', '/Users/gary.zhou/Documents/cloud_vision/service_account.json')
        

# Video faces detection

In [12]:
def detect_faces_video(images_path, creds_path):
    credentials = service_account.Credentials.from_service_account_file(creds_path)
    scoped_credentials = credentials.with_scopes(['https://www.googleapis.com/auth/cloud-platform'])
    client = vision.ImageAnnotatorClient(credentials=credentials)
    
    image_name=[filename for filename in os.listdir(images_path) if filename.endswith('.jpg')]
    video_name=[filename for filename in os.listdir(images_path) if filename.endswith('.mp4')]
    
    filenames =image_name   
    max=8
    index=0
    ind=0
    video_index=0
    ite_num=len(filenames)//max
    structured=[]
    
    for ite in range(ite_num+1):
        if ite!=ite_num:
            file_name=[file for file in filenames[index:index+max]]
            index=index+max
        else: 
            file_name=[file for file in filenames[max*ite_num:]]

        requests=[]
        for filename in file_name: 
            with io.open(images_path+filename, 'rb') as image_file:
                content = image_file.read()
                requests.append({
                    "image":{"content":content},
                    "features":[
                        {"type":"FACE_DETECTION"}
                    ]})
        resp = client.batch_annotate_images(requests)
        response = resp.responses
        
        for i in range(len(response)):
            if image_name[ind][:-8]!=video_name[video_index]:
                video_index+=1
                
            if not response[i].face_annotations:
                structured.append([image_name[ind],0,video_index])
                ind+=1
            else:
                re=response[i].face_annotations
                count=0
                for l in re:
                    count+=1
                structured.append([image_name[ind],count,video_index])
                ind+=1
                
    #combine group images to single row           
    df_image=pd.DataFrame(structured,columns=['name','count','video_index'])
    df_video=pd.DataFrame(video_name,columns=['name'])
    agg=df_image[df_image['count']>0].groupby('video_index')['count'].mean()
    df_agg=pd.Series.to_frame(agg)
    df=pd.concat([df_video,df_agg],axis=1,join='outer') 
    
    return(df.fillna(0).round())    
    

In [13]:
start_time = time.time()
df_stories_video=detect_faces_video('/Users/gary.zhou/Desktop/test/Stories_videos/', '/Users/gary.zhou/Documents/cloud_vision/service_account.json')
print("--- %s seconds ---" % (time.time() - start_time))   

--- 339.67152094841003 seconds ---


In [19]:
start_time = time.time()
df_In_feed_videos=detect_faces_video('/Users/gary.zhou/Desktop/test/In_feed_videos/', '/Users/gary.zhou/Documents/cloud_vision/service_account.json')
print("--- %s seconds ---" % (time.time() - start_time))   

--- 727.8709168434143 seconds ---


In [21]:
df_stories_video
df_stories_video['source']='Stories'
df_stories_video['file type']='videos'

In [22]:
df_In_feed_videos
df_In_feed_videos['source']='In_feed'
df_In_feed_videos['file type']='videos'

# Label_Data

In [5]:
start_time = time.time()
in_feed_images=detect_labels_image('/Users/gary.zhou/Desktop/test/In_feed_images/', '/Users/gary.zhou/Documents/cloud_vision/service_account.json')
print("--- %s seconds ---" % (time.time() - start_time))



--- 3420.898010969162 seconds ---


In [7]:
start_time = time.time()
stories_images=detect_labels_image('/Users/gary.zhou/Desktop/test/Stories_images/', '/Users/gary.zhou/Documents/cloud_vision/service_account.json')
print("--- %s seconds ---" % (time.time() - start_time))

--- 906.4998128414154 seconds ---


In [8]:
in_feed_images_label=pd.DataFrame(in_feed_images,columns=['filename','object','prob'])
stories_images_label=pd.DataFrame(stories_images,columns=['filename','object','prob'])

In [10]:

start_time = time.time()
in_feed_videos_label=detect_labels_video('/Users/gary.zhou/Desktop/test/In_feed_videos/', '/Users/gary.zhou/Documents/cloud_vision/service_account.json')
print("--- %s seconds ---" % (time.time() - start_time))

--- 2043.4189639091492 seconds ---


In [11]:
start_time = time.time()
stories_videos_label=detect_labels_video('/Users/gary.zhou/Desktop/test/Stories_videos/', '/Users/gary.zhou/Documents/cloud_vision/service_account.json')
print("--- %s seconds ---" % (time.time() - start_time))

--- 820.2081847190857 seconds ---


In [753]:
in_feed_videos_label

video_index                                           filename  \
0                 0  18577604_1892331500978391_409035823229435904_n...   
1                 0  18577604_1892331500978391_409035823229435904_n...   
2                 0  18577604_1892331500978391_409035823229435904_n...   
3                 0  18577604_1892331500978391_409035823229435904_n...   
4                 0  18577604_1892331500978391_409035823229435904_n...   
5                 0  18577604_1892331500978391_409035823229435904_n...   
6                 0  18577604_1892331500978391_409035823229435904_n...   
7                 0  18577604_1892331500978391_409035823229435904_n...   
8                 0  18577604_1892331500978391_409035823229435904_n...   
9                 0  18577604_1892331500978391_409035823229435904_n...   
10                0  18577604_1892331500978391_409035823229435904_n...   
11                0  18577604_1892331500978391_409035823229435904_n...   
12                0  18577604_1892331500978391_409035823229435904_n...   
13                0  18577604_1892331500978391_409035823229435904_n...   
14                0  18577604_1892331500978391_409035823229435904_n...   
15                0  18577604_1892331500978391_409035823229435904_n...   
16                0  18577604_1892331500978391_409035823229435904_n...   
17                0  18577604_1892331500978391_409035823229435904_n...   
18                0  18577604_1892331500978391_409035823229435904_n...   
19                0  18577604_1892331500978391_409035823229435904_n...   
20                0  18577604_1892331500978391_409035823229435904_n...   
21                0  18577604_1892331500978391_409035823229435904_n...   
22                0  18577604_1892331500978391_409035823229435904_n...   
23                0  18577604_1892331500978391_409035823229435904_n...   
24                0  18577604_1892331500978391_409035823229435904_n...   
25                0  18577604_1892331500978391_409035823229435904_n...   
26                0  18577604_1892331500978391_409035823229435904_n...   
27                0  18577604_1892331500978391_409035823229435904_n...   
28                0  18577604_1892331500978391_409035823229435904_n...   
29                0  18577604_1892331500978391_409035823229435904_n...   
30                0  18577604_1892331500978391_409035823229435904_n...   
31                0  18577604_1892331500978391_409035823229435904_n...   
32                0  18577604_1892331500978391_409035823229435904_n...   
33                0  18577604_1892331500978391_409035823229435904_n...   
34                0  18577604_1892331500978391_409035823229435904_n...   
35                0  18577604_1892331500978391_409035823229435904_n...   
36                0  18577604_1892331500978391_409035823229435904_n...   
37                0  18577604_1892331500978391_409035823229435904_n...   
38                0  18577604_1892331500978391_409035823229435904_n...   
39                0  18577604_1892331500978391_409035823229435904_n...   
40                0  18577604_1892331500978391_409035823229435904_n...   
41                0  18577604_1892331500978391_409035823229435904_n...   
42                0  18577604_1892331500978391_409035823229435904_n...   
43                0  18577604_1892331500978391_409035823229435904_n...   
44                0  18577604_1892331500978391_409035823229435904_n...   
45                0  18577604_1892331500978391_409035823229435904_n...   
46                0  18577604_1892331500978391_409035823229435904_n...   
47                0  18577604_1892331500978391_409035823229435904_n...   
48                0  18577604_1892331500978391_409035823229435904_n...   
49                0  18577604_1892331500978391_409035823229435904_n...   
50                0  18577604_1892331500978391_409035823229435904_n...   
51                0  18577604_1892331500978391_409035823229435904_n...   
52                0  18577604_1892331500978391_409035823229435904_n...   
53          

# Analysis(Face detection)

In [243]:
output5 = detect_labels_image('/Users/gary.zhou/Desktop/test/In_feed_videos/', '/Users/gary.zhou/Documents/cloud_vision/service_account.json')




In [244]:
df5=pd.DataFrame(output5,columns=['filename','object','probability'])
#df.head(100)


In [659]:
df_video=pd.concat([df_In_feed_videos,df_stories_video])
df_image=pd.concat([df_In_feed_image,df_stories_image])
df_video.rename(columns={"name":"filename"},inplace=True)
df_adidas=pd.concat([df_video,df_image])
df_adidas=df_adidas.reset_index()
df_adidas.drop(columns={'index'},inplace=True)

df_adidas_faces=df_adidas[df_adidas['count']>0]
df_adidas_faces.groupby(['source','file type']).sum()

count
source  file type        
In_feed image      2404.0
        videos      410.0
Stories image      1246.0
        videos      168.0

In [657]:
df_adidas_faces

filename  count   source  \
0     18577604_1892331500978391_409035823229435904_n...    1.0  In_feed   
3     20709060_1373290559442300_4163585733851900849_...    1.0  In_feed   
17    26190818_180139079404609_8534508039045120000_n...    6.0  In_feed   
32    26823437_880174705493555_6771469134208172032_n...    1.0  In_feed   
37    26879457_2012264632120224_2718545514743201792_...    2.0  In_feed   
42    27061180_1405322946263630_8348568485210619904_...    1.0  In_feed   
52    27079384_1818168901814480_5529524652751192064_...    1.0  In_feed   
53    27295759_545101369197762_1955576524870516736_n...    3.0  In_feed   
57    27305213_1809560672677867_372440618808377344_n...    4.0  In_feed   
60    27308242_146405982709778_666194576305815552_n.mp4    2.0  In_feed   
61    27309336_1564096663637734_2747190176353615872_...    1.0  In_feed   
62    27522733_1603127043108941_1430858428992978944_...    1.0  In_feed   
77    27529575_1858864664144236_1817884430321057792_...    1.0  In_feed   
80    27529620_170332203598405_4567956367291964561_n...    1.0  In_feed   
86    27531064_678695885587740_4759427910680235017_n...    1.0  In_feed   
88    27531803_2009506522704030_1254205011064258560_...    1.0  In_feed   
89    27532535_203951850341003_2137265296842431887_n...    1.0  In_feed   
90    27534021_184257735664853_3604167217127620608_n...    1.0  In_feed   
98    27667507_166324817345007_7955811620806676493_n...    1.0  In_feed   
100   27667864_2072176812997985_7708218868164621417_...    1.0  In_feed   
101   27667926_1441748245936033_2231435595559758779_...    1.0  In_feed   
105   27668145_154679435245780_4928687330591403612_n...    1.0  In_feed   
110   27669030_1445233938922953_4585728127169624268_...    1.0  In_feed   
112   27669056_345848239156905_129101623086546944_n.mp4    1.0  In_feed   
114   27669636_578486555843855_3564738392736268911_n...    1.0  In_feed   
116   27669870_1606808596075474_7072408138812217820_...    2.0  In_feed   
120   27670404_299857203875248_2546875604608267784_n...    2.0  In_feed   
129   27671736_2085220305096080_7925306373087166464_...    1.0  In_feed   
134   27674639_363272914152055_7937192634949304320_n...    3.0  In_feed   
136   27674737_404100820042314_365253630988648448_n.mp4    1.0  In_feed   
140   27675085_1984666908450300_2783741967245246464_...    4.0  In_feed   
141   27675117_1573449256102417_6115073248156109445_...    2.0  In_feed   
149   27675656_190565615046332_6241071507379636550_n...    1.0  In_feed   
155   27676108_1015229358629506_4855025314796929024_...    1.0  In_feed   
157   27676170_1593984207357543_7645706196845854720_...    1.0  In_feed   
159   27676437_213904662682051_5357431280706650987_n...    1.0  In_feed   
160   27676445_169063167058260_5632085371537543020_n...    1.0  In_feed   
161   27676479_539190929795568_6418815940833574912_n...    1.0  In_feed   
163   27676524_408819239582996_4006756964460658688_n...    2.0  In_feed   
164   27676682_2511388732418721_11172355803683117_n.mp4    1.0  In_feed   
166   27676710_415626168895080_6896418263881572286_n...    1.0  In_feed   
168   27676971_169805783644272_8952757795485122560_n...    1.0  In_feed   
169   27677002_416907615415742_6908090751388022075_n...    1.0  In_feed   
170   27677371_189702295131903_6800881331225031247_n...    1.0  In_feed   
173   27677629_1068468589960643_4680316308338870480_...    1.0  In_feed   
175   27677736_1727624913927733_2162228690126137138_...    1.0  In_feed   
176   27677741_1604090669710311_1111375981009960960_...    2.0  In_feed   
181   27678079_2011972242407300_6329991086529839104_...    1.0  In_feed   
184   27678172_2051246555154339_1537620821131832913_...    1.0  In_feed   
188   27678298_157421584916980_7006678420158005262_n...    1.0  In_feed   
189   27678330_2048031318810166_114790988005911525_n...    2.0  In_feed   
192   27678649_417766552000518_7555205137065574400_n...    1.0  In_feed   
194   27678773_162050777923713_6490028547669440296_n...    1.0  In_feed 

# Analysis (label)

In [12]:
image_label=pd.concat([in_feed_images_label,stories_images_label])

In [13]:
image_label

filename  \
0      24175506_169512276977734_5210213780121714688_n...   
1      24175506_169512276977734_5210213780121714688_n...   
2      24175506_169512276977734_5210213780121714688_n...   
3      24175506_169512276977734_5210213780121714688_n...   
4      24175506_169512276977734_5210213780121714688_n...   
5      24175506_169512276977734_5210213780121714688_n...   
6      24175506_169512276977734_5210213780121714688_n...   
7      24175506_169512276977734_5210213780121714688_n...   
8      24175506_169512276977734_5210213780121714688_n...   
9      24175506_169512276977734_5210213780121714688_n...   
10     25036659_1527256927323801_6735676178138398720_...   
11     25036659_1527256927323801_6735676178138398720_...   
12     25036659_1527256927323801_6735676178138398720_...   
13     25036659_1527256927323801_6735676178138398720_...   
14     25036659_1527256927323801_6735676178138398720_...   
15     25036659_1527256927323801_6735676178138398720_...   
16     25036659_1527256927323801_6735676178138398720_...   
17     25036659_1527256927323801_6735676178138398720_...   
18     25036659_1527256927323801_6735676178138398720_...   
19     25036659_1527256927323801_6735676178138398720_...   
20     25037016_253548621851555_3636738028602392576_n...   
21     25037016_253548621851555_3636738028602392576_n...   
22     25037016_253548621851555_3636738028602392576_n...   
23     25037016_253548621851555_3636738028602392576_n...   
24     25037016_253548621851555_3636738028602392576_n...   
25     25037016_253548621851555_3636738028602392576_n...   
26     25037016_253548621851555_3636738028602392576_n...   
27     25038595_1618907854862436_2293914648082120704_...   
28     25038595_1618907854862436_2293914648082120704_...   
29     25038595_1618907854862436_2293914648082120704_...   
...                                                  ...   
18784  34982772_459296434511211_5986618428423667712_n...   
18785  34982772_459296434511211_5986618428423667712_n...   
18786  34982772_459296434511211_5986618428423667712_n...   
18787  34982772_459296434511211_5986618428423667712_n...   
18788  34982772_459296434511211_5986618428423667712_n...   
18789  34982772_459296434511211_5986618428423667712_n...   
18790  34983487_469036403545594_4384034012797075456_n...   
18791  34983487_469036403545594_4384034012797075456_n...   
18792  34983487_469036403545594_4384034012797075456_n...   
18793  34983487_469036403545594_4384034012797075456_n...   
18794  35001542_1682122721902587_345911842771566592_n...   
18795  35001542_1682122721902587_345911842771566592_n...   
18796  35001542_1682122721902587_345911842771566592_n...   
18797  35001542_1682122721902587_345911842771566592_n...   
18798  35001542_1682122721902587_345911842771566592_n...   
18799  35001542_1682122721902587_345911842771566592_n...   
18800  35001542_1682122721902587_345911842771566592_n...   
18801  35001542_1682122721902587_345911842771566592_n...   
18802  35001542_1682122721902587_345911842771566592_n...   
18803  35001542_1682122721902587_345911842771566592_n...   
18804  35520833_1749957281751566_6871232690394234880_...   
18805  35520833_1749957281751566_6871232690394234880_...   
18806  35520833_1749957281751566_6871232690394234880_...   
18807  35520833_1749957281751566_6871232690394234880_...   
18808  35520833_1749957281751566_6871232690394234880_...   
18809  35520833_1749957281751566_6871232690394234880_...   
18810  35520833_1749957281751566_6871232690394234880_...   
18811  35520833_1749957281751566_6871232690394234880_...   
18812  35520833_1749957281751566_6871232690394234880_...   
18813  35520833_1749957281751566_6871232690394234880_...   

                       object      prob  
0                     t shirt  0.959756  
1                    footwear  0.911549  
2                  sportswear  0.885956  
3                    shoulder  0.797446  
4                        shoe  0.791966  
5                      sleeve  0.765466  
6                   outerwear  0.

In [14]:
def combine_images(df):
    duplicate=[]
    video_list=[]
    video_index=0
    Object=''
    for i in range(len(df)):
        Object=df['object'].loc[i]
        if df['video_index'].loc[i]!=video_index:
            video_index+=1
            duplicate=[]
        if (df['probability'].loc[i]>0.6) & (Object not in duplicate):
            duplicate.append(df['object'].loc[i])
            video_list.append([video_index,df['filename'].loc[i],df['object'].loc[i],df['probability'].loc[i]])
            
    df_final=pd.DataFrame(video_list,columns=['id','filename','object','prob'])
    return df_final
        

In [15]:
df_01=combine_images(in_feed_videos_label)


In [16]:
df_02=combine_images(stories_videos_label)

In [17]:
video_label=pd.concat([df_01,df_02])

In [19]:
video_label=video_label.drop(columns=['id'])

In [69]:
df_f=pd.concat([image_label,video_label])

In [70]:
df_f

filename  \
0      24175506_169512276977734_5210213780121714688_n...   
1      24175506_169512276977734_5210213780121714688_n...   
2      24175506_169512276977734_5210213780121714688_n...   
3      24175506_169512276977734_5210213780121714688_n...   
4      24175506_169512276977734_5210213780121714688_n...   
5      24175506_169512276977734_5210213780121714688_n...   
6      24175506_169512276977734_5210213780121714688_n...   
7      24175506_169512276977734_5210213780121714688_n...   
8      24175506_169512276977734_5210213780121714688_n...   
9      24175506_169512276977734_5210213780121714688_n...   
10     25036659_1527256927323801_6735676178138398720_...   
11     25036659_1527256927323801_6735676178138398720_...   
12     25036659_1527256927323801_6735676178138398720_...   
13     25036659_1527256927323801_6735676178138398720_...   
14     25036659_1527256927323801_6735676178138398720_...   
15     25036659_1527256927323801_6735676178138398720_...   
16     25036659_1527256927323801_6735676178138398720_...   
17     25036659_1527256927323801_6735676178138398720_...   
18     25036659_1527256927323801_6735676178138398720_...   
19     25036659_1527256927323801_6735676178138398720_...   
20     25037016_253548621851555_3636738028602392576_n...   
21     25037016_253548621851555_3636738028602392576_n...   
22     25037016_253548621851555_3636738028602392576_n...   
23     25037016_253548621851555_3636738028602392576_n...   
24     25037016_253548621851555_3636738028602392576_n...   
25     25037016_253548621851555_3636738028602392576_n...   
26     25037016_253548621851555_3636738028602392576_n...   
27     25038595_1618907854862436_2293914648082120704_...   
28     25038595_1618907854862436_2293914648082120704_...   
29     25038595_1618907854862436_2293914648082120704_...   
...                                                  ...   
11669  34421959_177985642865557_4751565497733801106_n...   
11670  34421959_177985642865557_4751565497733801106_n...   
11671  34421959_177985642865557_4751565497733801106_n...   
11672  34790539_176227653012566_9140152702550553127_n...   
11673  34790539_176227653012566_9140152702550553127_n...   
11674  34790539_176227653012566_9140152702550553127_n...   
11675  34790539_176227653012566_9140152702550553127_n...   
11676  34790539_176227653012566_9140152702550553127_n...   
11677  34790539_176227653012566_9140152702550553127_n...   
11678  34790539_176227653012566_9140152702550553127_n...   
11679  34790539_176227653012566_9140152702550553127_n...   
11680  34790539_176227653012566_9140152702550553127_n...   
11681  34790539_176227653012566_9140152702550553127_n...   
11682  34790539_176227653012566_9140152702550553127_n...   
11683  34790539_176227653012566_9140152702550553127_n...   
11684  34790539_176227653012566_9140152702550553127_n...   
11685  34790539_176227653012566_9140152702550553127_n...   
11686  34790539_176227653012566_9140152702550553127_n...   
11687  34790539_176227653012566_9140152702550553127_n...   
11688  34790539_176227653012566_9140152702550553127_n...   
11689  34790539_176227653012566_9140152702550553127_n...   
11690  34790539_176227653012566_9140152702550553127_n...   
11691  34790539_176227653012566_9140152702550553127_n...   
11692  34790539_176227653012566_9140152702550553127_n...   
11693  34790539_176227653012566_9140152702550553127_n...   
11694  34790539_176227653012566_9140152702550553127_n...   
11695  34790539_176227653012566_9140152702550553127_n...   
11696  34790539_176227653012566_9140152702550553127_n...   
11697  34790539_176227653012566_9140152702550553127_n...   
11698  34790539_176227653012566_9140152702550553127_n...   

                       object      prob  
0                     t shirt  0.959756  
1                    footwear  0.911549  
2                  sportswear  0.885956  
3                    shoulder  0.797446  
4                        shoe  0.791966  
5                      sleeve  0.765466  
6                   outerwear  0.

In [71]:
df_f=df_f.reset_index()

In [72]:
df_f=df_f.drop(columns=['index'])

In [73]:
df_f

filename  \
0      24175506_169512276977734_5210213780121714688_n...   
1      24175506_169512276977734_5210213780121714688_n...   
2      24175506_169512276977734_5210213780121714688_n...   
3      24175506_169512276977734_5210213780121714688_n...   
4      24175506_169512276977734_5210213780121714688_n...   
5      24175506_169512276977734_5210213780121714688_n...   
6      24175506_169512276977734_5210213780121714688_n...   
7      24175506_169512276977734_5210213780121714688_n...   
8      24175506_169512276977734_5210213780121714688_n...   
9      24175506_169512276977734_5210213780121714688_n...   
10     25036659_1527256927323801_6735676178138398720_...   
11     25036659_1527256927323801_6735676178138398720_...   
12     25036659_1527256927323801_6735676178138398720_...   
13     25036659_1527256927323801_6735676178138398720_...   
14     25036659_1527256927323801_6735676178138398720_...   
15     25036659_1527256927323801_6735676178138398720_...   
16     25036659_1527256927323801_6735676178138398720_...   
17     25036659_1527256927323801_6735676178138398720_...   
18     25036659_1527256927323801_6735676178138398720_...   
19     25036659_1527256927323801_6735676178138398720_...   
20     25037016_253548621851555_3636738028602392576_n...   
21     25037016_253548621851555_3636738028602392576_n...   
22     25037016_253548621851555_3636738028602392576_n...   
23     25037016_253548621851555_3636738028602392576_n...   
24     25037016_253548621851555_3636738028602392576_n...   
25     25037016_253548621851555_3636738028602392576_n...   
26     25037016_253548621851555_3636738028602392576_n...   
27     25038595_1618907854862436_2293914648082120704_...   
28     25038595_1618907854862436_2293914648082120704_...   
29     25038595_1618907854862436_2293914648082120704_...   
...                                                  ...   
91110  34421959_177985642865557_4751565497733801106_n...   
91111  34421959_177985642865557_4751565497733801106_n...   
91112  34421959_177985642865557_4751565497733801106_n...   
91113  34790539_176227653012566_9140152702550553127_n...   
91114  34790539_176227653012566_9140152702550553127_n...   
91115  34790539_176227653012566_9140152702550553127_n...   
91116  34790539_176227653012566_9140152702550553127_n...   
91117  34790539_176227653012566_9140152702550553127_n...   
91118  34790539_176227653012566_9140152702550553127_n...   
91119  34790539_176227653012566_9140152702550553127_n...   
91120  34790539_176227653012566_9140152702550553127_n...   
91121  34790539_176227653012566_9140152702550553127_n...   
91122  34790539_176227653012566_9140152702550553127_n...   
91123  34790539_176227653012566_9140152702550553127_n...   
91124  34790539_176227653012566_9140152702550553127_n...   
91125  34790539_176227653012566_9140152702550553127_n...   
91126  34790539_176227653012566_9140152702550553127_n...   
91127  34790539_176227653012566_9140152702550553127_n...   
91128  34790539_176227653012566_9140152702550553127_n...   
91129  34790539_176227653012566_9140152702550553127_n...   
91130  34790539_176227653012566_9140152702550553127_n...   
91131  34790539_176227653012566_9140152702550553127_n...   
91132  34790539_176227653012566_9140152702550553127_n...   
91133  34790539_176227653012566_9140152702550553127_n...   
91134  34790539_176227653012566_9140152702550553127_n...   
91135  34790539_176227653012566_9140152702550553127_n...   
91136  34790539_176227653012566_9140152702550553127_n...   
91137  34790539_176227653012566_9140152702550553127_n...   
91138  34790539_176227653012566_9140152702550553127_n...   
91139  34790539_176227653012566_9140152702550553127_n...   

                       object      prob  
0                     t shirt  0.959756  
1                    footwear  0.911549  
2                  sportswear  0.885956  
3                    shoulder  0.797446  
4                        shoe  0.791966  
5                      sleeve  0.765466  
6                   outerwear  0.

In [74]:
def search_bucket(df):
    shoes=['shoe','shoes','footwear','outdoor shoe','sneakers','walking shoe','sportswear','athletic shoe','running shoe','tennis shoe','boot']
    apparel=['apparel','outerwear','t shirt','sleeve','jeans','jacket','clothing','trousers','apparel']
    color=['color','blue','black','purple','red','yellow','black and white','white','pink','green','electric blue','violet','orange','magenta']
    concert=['concert','rock concert']
    photograph=['snapshot','photography','monochrome photography']
    new_object=[]
    for row in df.itertuples():
        if row.object in shoes:
            new_object.append('shoes')
            continue
        if row.object in apparel:
            new_object.append('apparel')
            continue
        if row.object in color:
            new_object.append('color')
            continue
        if row.object in concert:
            new_object.append('concert')
            continue
        if row.object in photograph:
            new_object.append('photograph')
            continue
        new_object.append(row.object)
    df['object']=pd.Series(new_object)
    return df
    
    
    
    

In [75]:
df_bucket=search_bucket(df_f)

In [904]:
df_anal=df_bucket.drop_duplicates(['filename','object'])
aaa=df_anal[df_anal.prob>0.70].groupby('object').count().sort_values('filename',ascending=False)
aaa=aaa.reset_index()
aaa[aaa['object']=='shoes']

object  filename  prob
1  shoes      1810  1810

In [77]:
df_ana=df_bucket

In [795]:
#result=df_ana[df_ana.prob>0.70].groupby('object').count().sort_values('filename',ascending=False)


In [906]:
#df_ana[df_ana.prob>0.70].groupby('object').count().sort_values('filename',ascending=False)


In [78]:
video_ind=0
ind_row=[]
video=df_ana['filename'].loc[0]
for row in df_ana.itertuples():
    if row.filename!=video:
        video=row.filename
        video_ind+=1
    ind_row.append(video_ind)

    


In [80]:
df_ana

filename             object  \
0      24175506_169512276977734_5210213780121714688_n...            apparel   
1      24175506_169512276977734_5210213780121714688_n...              shoes   
2      24175506_169512276977734_5210213780121714688_n...              shoes   
3      24175506_169512276977734_5210213780121714688_n...           shoulder   
4      24175506_169512276977734_5210213780121714688_n...              shoes   
5      24175506_169512276977734_5210213780121714688_n...            apparel   
6      24175506_169512276977734_5210213780121714688_n...            apparel   
7      24175506_169512276977734_5210213780121714688_n...            product   
8      24175506_169512276977734_5210213780121714688_n...         recreation   
9      24175506_169512276977734_5210213780121714688_n...           material   
10     25036659_1527256927323801_6735676178138398720_...              color   
11     25036659_1527256927323801_6735676178138398720_...               text   
12     25036659_1527256927323801_6735676178138398720_...              color   
13     25036659_1527256927323801_6735676178138398720_...               font   
14     25036659_1527256927323801_6735676178138398720_...         photograph   
15     25036659_1527256927323801_6735676178138398720_...         monochrome   
16     25036659_1527256927323801_6735676178138398720_...               logo   
17     25036659_1527256927323801_6735676178138398720_...               area   
18     25036659_1527256927323801_6735676178138398720_...              night   
19     25036659_1527256927323801_6735676178138398720_...           darkness   
20     25037016_253548621851555_3636738028602392576_n...       music artist   
21     25037016_253548621851555_3636738028602392576_n...            product   
22     25037016_253548621851555_3636738028602392576_n...        performance   
23     25037016_253548621851555_3636738028602392576_n...         gold medal   
24     25037016_253548621851555_3636738028602392576_n...  competition event   
25     25037016_253548621851555_3636738028602392576_n...            singing   
26     25037016_253548621851555_3636738028602392576_n...                fun   
27     25038595_1618907854862436_2293914648082120704_...           landmark   
28     25038595_1618907854862436_2293914648082120704_...           building   
29     25038595_1618907854862436_2293914648082120704_...              night   
...                                                  ...                ...   
91110  34421959_177985642865557_4751565497733801106_n...              color   
91111  34421959_177985642865557_4751565497733801106_n...       social group   
91112  34421959_177985642865557_4751565497733801106_n...                gym   
91113  34790539_176227653012566_9140152702550553127_n...            product   
91114  34790539_176227653012566_9140152702550553127_n...                fan   
91115  34790539_176227653012566_9140152702550553127_n...                arm   
91116  34790539_176227653012566_9140152702550553127_n...           headgear   
91117  34790539_176227653012566_9140152702550553127_n...             muscle   
91118  34790539_176227653012566_9140152702550553127_n...             people   
91119  34790539_176227653012566_9140152702550553127_n...              child   
91120  34790539_176227653012566_9140152702550553127_n...                day   
91121  34790539_176227653012566_9140152702550553127_n...                fun   
91122  34790539_176227653012566_9140152702550553127_n...               girl   
91123  34790539_176227653012566_9140152702550553127_n...         photograph   
91124  34790539_176227653012566_9140152702550553127_n...            toddler   
91125  34790539_176227653012566_9140152702550553127_n...               hand   
91126  34790539_176227653012566_9140152702550553127_n...              mouth   
91127  34790539_176227653012566_9140152702550553127_n...        interaction   
91128  34790539_176227653012566_9140152702550553127_n...          hairstyle   
91129  34790539_176

In [81]:
se2=pd.Series(ind_row)
df_ana['ind']=se2
df_ori=df_ana.drop_duplicates(['filename','object'])

In [83]:
ana=df_ori[df_ori.prob>0.75].groupby('object').count().sort_values('filename',ascending=False)



In [86]:
df_ori.to_csv('label_ori.csv')

In [82]:
df_ori=df_ori[df_ori.prob>0.75]
df_ori


filename             object  \
0      24175506_169512276977734_5210213780121714688_n...            apparel   
1      24175506_169512276977734_5210213780121714688_n...              shoes   
3      24175506_169512276977734_5210213780121714688_n...           shoulder   
10     25036659_1527256927323801_6735676178138398720_...              color   
11     25036659_1527256927323801_6735676178138398720_...               text   
13     25036659_1527256927323801_6735676178138398720_...               font   
20     25037016_253548621851555_3636738028602392576_n...       music artist   
27     25038595_1618907854862436_2293914648082120704_...           landmark   
28     25038595_1618907854862436_2293914648082120704_...           building   
29     25038595_1618907854862436_2293914648082120704_...              night   
30     25038595_1618907854862436_2293914648082120704_...  metropolitan area   
31     25038595_1618907854862436_2293914648082120704_...       architecture   
32     25038595_1618907854862436_2293914648082120704_...         metropolis   
33     25038595_1618907854862436_2293914648082120704_...         urban area   
34     25038595_1618907854862436_2293914648082120704_...               city   
37     26065548_150626812383272_1999807438114521088_n...              color   
38     26065548_150626812383272_1999807438114521088_n...               text   
40     26065548_150626812383272_1999807438114521088_n...               font   
41     26065548_150626812383272_1999807438114521088_n...         monochrome   
47     26071176_367047447092359_4495207179669733376_n...               text   
48     26071176_367047447092359_4495207179669733376_n...               font   
49     26071176_367047447092359_4495207179669733376_n...              color   
61     26156256_209837116230386_9149447098410729472_n...              color   
63     26156256_209837116230386_9149447098410729472_n...         photograph   
64     26156256_209837116230386_9149447098410729472_n...         atmosphere   
66     26156256_209837116230386_9149447098410729472_n...         monochrome   
71     26156508_1850601364963475_3292394274095628288_...            apparel   
72     26156508_1850601364963475_3292394274095628288_...              shoes   
73     26156508_1850601364963475_3292394274095628288_...              child   
74     26156508_1850601364963475_3292394274095628288_...                boy   
...                                                  ...                ...   
91100  34421959_177985642865557_4751565497733801106_n...        sport venue   
91105  34421959_177985642865557_4751565497733801106_n...                man   
91106  34421959_177985642865557_4751565497733801106_n...                day   
91107  34421959_177985642865557_4751565497733801106_n...               girl   
91108  34421959_177985642865557_4751565497733801106_n...              youth   
91109  34421959_177985642865557_4751565497733801106_n...            product   
91110  34421959_177985642865557_4751565497733801106_n...              color   
91111  34421959_177985642865557_4751565497733801106_n...       social group   
91113  34790539_176227653012566_9140152702550553127_n...            product   
91114  34790539_176227653012566_9140152702550553127_n...                fan   
91115  34790539_176227653012566_9140152702550553127_n...                arm   
91118  34790539_176227653012566_9140152702550553127_n...             people   
91119  34790539_176227653012566_9140152702550553127_n...              child   
91120  34790539_176227653012566_9140152702550553127_n...                day   
91121  34790539_176227653012566_9140152702550553127_n...                fun   
91122  34790539_176227653012566_9140152702550553127_n...               girl   
91123  34790539_176227653012566_9140152702550553127_n...         photograph   
91124  34790539_176227653012566_9140152702550553127_n...            toddler   
91125  34790539_176227653012566_9140152702550553127_n...               hand   
91126  34790539_176

filename object      prob  ind  \
10  25036659_1527256927323801_6735676178138398720_...  color  0.949924    1   
11  25036659_1527256927323801_6735676178138398720_...   text  0.947646    1   
13  25036659_1527256927323801_6735676178138398720_...   font  0.884107    1   

   new_object final_object  
10      color        color  
11       text         text  
13       font         font

filename  \
0      24175506_169512276977734_5210213780121714688_n...   
1      24175506_169512276977734_5210213780121714688_n...   
3      24175506_169512276977734_5210213780121714688_n...   
10     25036659_1527256927323801_6735676178138398720_...   
11     25036659_1527256927323801_6735676178138398720_...   
13     25036659_1527256927323801_6735676178138398720_...   
20     25037016_253548621851555_3636738028602392576_n...   
27     25038595_1618907854862436_2293914648082120704_...   
28     25038595_1618907854862436_2293914648082120704_...   
29     25038595_1618907854862436_2293914648082120704_...   
30     25038595_1618907854862436_2293914648082120704_...   
31     25038595_1618907854862436_2293914648082120704_...   
32     25038595_1618907854862436_2293914648082120704_...   
33     25038595_1618907854862436_2293914648082120704_...   
34     25038595_1618907854862436_2293914648082120704_...   
37     26065548_150626812383272_1999807438114521088_n...   
38     26065548_150626812383272_1999807438114521088_n...   
40     26065548_150626812383272_1999807438114521088_n...   
41     26065548_150626812383272_1999807438114521088_n...   
47     26071176_367047447092359_4495207179669733376_n...   
48     26071176_367047447092359_4495207179669733376_n...   
49     26071176_367047447092359_4495207179669733376_n...   
61     26156256_209837116230386_9149447098410729472_n...   
63     26156256_209837116230386_9149447098410729472_n...   
64     26156256_209837116230386_9149447098410729472_n...   
66     26156256_209837116230386_9149447098410729472_n...   
71     26156508_1850601364963475_3292394274095628288_...   
72     26156508_1850601364963475_3292394274095628288_...   
73     26156508_1850601364963475_3292394274095628288_...   
74     26156508_1850601364963475_3292394274095628288_...   
76     26156508_1850601364963475_3292394274095628288_...   
81     26157545_166536237297416_6613292107241095168_n...   
82     26157545_166536237297416_6613292107241095168_n...   
83     26157545_166536237297416_6613292107241095168_n...   
84     26157545_166536237297416_6613292107241095168_n...   
85     26157545_166536237297416_6613292107241095168_n...   
86     26157545_166536237297416_6613292107241095168_n...   
91     26182531_805687959617651_1692723817685712896_n...   
94     26182531_805687959617651_1692723817685712896_n...   
95     26182531_805687959617651_1692723817685712896_n...   
99     26183494_2006709782883913_6054144376697782272_...   
100    26183494_2006709782883913_6054144376697782272_...   
101    26183494_2006709782883913_6054144376697782272_...   
109    26185706_1322534207851539_6900034333059317760_...   
110    26185706_1322534207851539_6900034333059317760_...   
111    26185706_1322534207851539_6900034333059317760_...   
112    26185706_1322534207851539_6900034333059317760_...   
113    26185706_1322534207851539_6900034333059317760_...   
114    26185706_1322534207851539_6900034333059317760_...   
115    26185706_1322534207851539_6900034333059317760_...   
117    26185706_1322534207851539_6900034333059317760_...   
119    26185887_151435138779037_8893950510562803712_n...   
120    26185887_151435138779037_8893950510562803712_n...   
122    26185887_151435138779037_8893950510562803712_n...   
123    26185887_151435138779037_8893950510562803712_n...   
135    26187364_161283164514079_5965319131552022528_n...   
136    26187364_161283164514079_5965319131552022528_n...   
137    26187364_161283164514079_5965319131552022528_n...   
138    26187364_161283164514079_5965319131552022528_n...   
142    26226685_176500409748444_2049408086975709184_n...   
143    26226685_176500409748444_2049408086975709184_n...   
144    26226685_176500409748444_2049408086975709184_n...   
145    26226685_176500409748444_2049408086975709184_n...   
146    26226685_176500409748444_2049408086975709184_n...   
147    26226685_176500409748444_2049408086975709184_n...   
154    26268515_1841349675937707_4045261548132761600_...   
155    26268515_184134967593

In [1244]:
df_ori['last']=0
df_ori['last'].loc[91138]=1
df_ori

/anaconda3/lib/python3.6/site-packages/pandas/core/indexing.py:189: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)


filename  \
0      24175506_169512276977734_5210213780121714688_n...   
1      24175506_169512276977734_5210213780121714688_n...   
3      24175506_169512276977734_5210213780121714688_n...   
10     25036659_1527256927323801_6735676178138398720_...   
11     25036659_1527256927323801_6735676178138398720_...   
13     25036659_1527256927323801_6735676178138398720_...   
20     25037016_253548621851555_3636738028602392576_n...   
27     25038595_1618907854862436_2293914648082120704_...   
28     25038595_1618907854862436_2293914648082120704_...   
29     25038595_1618907854862436_2293914648082120704_...   
30     25038595_1618907854862436_2293914648082120704_...   
31     25038595_1618907854862436_2293914648082120704_...   
32     25038595_1618907854862436_2293914648082120704_...   
33     25038595_1618907854862436_2293914648082120704_...   
34     25038595_1618907854862436_2293914648082120704_...   
37     26065548_150626812383272_1999807438114521088_n...   
38     26065548_150626812383272_1999807438114521088_n...   
40     26065548_150626812383272_1999807438114521088_n...   
41     26065548_150626812383272_1999807438114521088_n...   
47     26071176_367047447092359_4495207179669733376_n...   
48     26071176_367047447092359_4495207179669733376_n...   
49     26071176_367047447092359_4495207179669733376_n...   
61     26156256_209837116230386_9149447098410729472_n...   
63     26156256_209837116230386_9149447098410729472_n...   
64     26156256_209837116230386_9149447098410729472_n...   
66     26156256_209837116230386_9149447098410729472_n...   
71     26156508_1850601364963475_3292394274095628288_...   
72     26156508_1850601364963475_3292394274095628288_...   
73     26156508_1850601364963475_3292394274095628288_...   
74     26156508_1850601364963475_3292394274095628288_...   
76     26156508_1850601364963475_3292394274095628288_...   
81     26157545_166536237297416_6613292107241095168_n...   
82     26157545_166536237297416_6613292107241095168_n...   
83     26157545_166536237297416_6613292107241095168_n...   
84     26157545_166536237297416_6613292107241095168_n...   
85     26157545_166536237297416_6613292107241095168_n...   
86     26157545_166536237297416_6613292107241095168_n...   
91     26182531_805687959617651_1692723817685712896_n...   
94     26182531_805687959617651_1692723817685712896_n...   
95     26182531_805687959617651_1692723817685712896_n...   
99     26183494_2006709782883913_6054144376697782272_...   
100    26183494_2006709782883913_6054144376697782272_...   
101    26183494_2006709782883913_6054144376697782272_...   
109    26185706_1322534207851539_6900034333059317760_...   
110    26185706_1322534207851539_6900034333059317760_...   
111    26185706_1322534207851539_6900034333059317760_...   
112    26185706_1322534207851539_6900034333059317760_...   
113    26185706_1322534207851539_6900034333059317760_...   
114    26185706_1322534207851539_6900034333059317760_...   
115    26185706_1322534207851539_6900034333059317760_...   
117    26185706_1322534207851539_6900034333059317760_...   
119    26185887_151435138779037_8893950510562803712_n...   
120    26185887_151435138779037_8893950510562803712_n...   
122    26185887_151435138779037_8893950510562803712_n...   
123    26185887_151435138779037_8893950510562803712_n...   
135    26187364_161283164514079_5965319131552022528_n...   
136    26187364_161283164514079_5965319131552022528_n...   
137    26187364_161283164514079_5965319131552022528_n...   
138    26187364_161283164514079_5965319131552022528_n...   
142    26226685_176500409748444_2049408086975709184_n...   
143    26226685_176500409748444_2049408086975709184_n...   
144    26226685_176500409748444_2049408086975709184_n...   
145    26226685_176500409748444_2049408086975709184_n...   
146    26226685_176500409748444_2049408086975709184_n...   
147    26226685_176500409748444_2049408086975709184_n...   
154    26268515_1841349675937707_4045261548132761600_...   
155    26268515_184134967593

# Label matrix

In [1234]:
matrix_object=ana[ana.filename>199].reset_index()['object'].tolist()

In [1259]:
def matrix_generate(matrix_list,df):
    df_final=pd.DataFrame()
    for obj in matrix_object:
        column=[]
        for obj_occur in matrix_object:
            num=concur(obj,obj_occur,df)
            column.append(num)
        df_final[obj]=column
    return df_final

csv_print=matrix_generate(matrix_object,df_ori)

        
        
        
    

In [1260]:
csv_print.to_csv('label_matrix.csv')

# Concert

In [1159]:
con=['light','entertainment','stage','performance','event','crowd','lighting','audience','performing arts','singing','performance art','guitarist','music artist','music','musician','disco','nightclub','pop music','drums','festival','drummer','public event','singer']

In [1160]:
conc=[row.ind for row in df_ana.itertuples() if (row.object=='concert')&(row.prob>0.55)]
len(conc)



2109

In [1161]:
file_index=0
word_list=[]
for row in df_ana.itertuples():
    if row.ind!=file_index:
        file_index+=1
    if (row.object in con)&(file_index in conc):
        word_list.append('concert')
    else:
        word_list.append(row.object)

In [1162]:
se3=pd.Series(word_list)
df_ana['new_object']=se3

In [1163]:
new_bucket=['light','entertainment','stage','performance','event','crowd','lighting','auidence','performing arts','performance art']

In [1185]:
new_con=[row.ind for row in df_ana.itertuples() if row.new_object in ['concert','auditorium','singer','singing','music artist','drums','musical theatre','musical instrument','performing arts','performance art']]

In [1186]:
file_index=0
word_list2=[]
for row in df_ana.itertuples():
    if row.ind!=file_index:
        file_index+=1
    if (row.new_object in new_bucket)&(file_index in new_con):
        word_list2.append('concert')
    else:
        word_list2.append(row.new_object)
        

In [1187]:
se4=pd.Series(word_list2)
df_ana['final_object']=se4

In [1188]:
df=df_ana.drop_duplicates(['filename','final_object'])

In [1192]:
len(df[df.prob>0.75])

33839

In [1198]:
final_label=df[df.prob>0.6].groupby('final_object').count().sort_values('filename',ascending=False)
final_label.head(100)

filename  object  prob   ind  new_object
final_object                                                           
color                              3925    3925  3925  3925        3925
product                            2370    2370  2370  2370        2370
shoes                              1957    1957  1957  1957        1957
concert                            1538    1538  1538  1538        1538
fun                                1443    1443  1443  1443        1443
font                               1130    1130  1130  1130        1130
darkness                            932     932   932   932         932
structure                           895     895   895   895         895
photograph                          893     893   893   893         893
night                               848     848   848   848         848
sky                                 767     767   767   767         767
design                              727     727   727   727         727
light                               685     685   685   685         685
people                              671     671   671   671         671
text                                623     623   623   623         623
technology                          605     605   605   605         605
recreation                          589     589   589   589         589
sport venue                         555     555   555   555         555
apparel                             547     547   547   547         547
crowd                               530     530   530   530         530
line                                524     524   524   524         524
art                                 499     499   499   499         499
advertising                         486     486   486   486         486
mode of transport                   476     476   476   476         476
cool                                447     447   447   447         447
girl                                437     437   437   437         437
competition event                   431     431   431   431         431
display device                      414     414   414   414         414
atmosphere                          408     408   408   408         408
city                                401     401   401   401         401
event                               394     394   394   394         394
monochrome                          378     378   378   378         378
day                                 365     365   365   365         365
lighting                            343     343   343   343         343
arm                                 333     333   333   333         333
sports                              332     332   332   332         332
music venue                         331     331   331   331         331
facial hair                         331     331   331   331         331
games                               312     312   312   312         312
player                              311     311   311   311         311
man                                 310     310   310   310         310
car                                 299     299   299   299         299
muscle                              296     296   296   296         296
fashion                             290     290   290   290         290
brand                               285     285   285   285         285
vehicle                             276     276   276   276         276
team sport                          270     270   270   270         270
hand                                258     258   258   258         258
water                               255     255   255   255         255
social group                        251     251   251   251         251
standing                            238     238   238   238         238
material                            231     231   231   231         231
public event                        227     227   227   227         227
pattern                             225     225   225   225         225

In [1191]:
final_label.to_csv('label_final.csv')

In [1178]:
pwd

'/Users/gary.zhou/Documents/cloud_vision'

In [1204]:
len(df[df.final_object=='selfie'])

84

In [1194]:
#df[df.ind==2254]

In [1205]:
#df[(df.final_object=='selfie')&(df.prob>.75)]

In [1196]:
#for i in con:
#    print(pd.Series.to_string(re[re['new_object']==i]['index'])[2:])


# Others

In [14]:
keywords=['t shirt','footwear','sportswear','shoe','outdoor shoe','sneakers']
#df[df['object']=='landmark']
#df[df['filename']==46]
        

In [15]:
filenames = [filename for filename in os.listdir('/Users/gary.zhou/desktop/test/Core_images/') if 'DS_Store' not in filename]

In [16]:
n1=1
jpg='.jpg'
for name in filenames:
    os.renames(old=name,new=str(n1)+jpg)
    n1=n1+1

FileNotFoundError: [Errno 2] No such file or directory: '24175506_169512276977734_5210213780121714688_n.jpg' -> '1.jpg'

In [245]:
cd desktop/test/Stores_images/


/Users/gary.zhou/Desktop/test/Stores_images


In [31]:
count=0
num_images=set(df2['filename'])
for i in num_images:
    index_min=df2[df2['filename']==i].index[0]
    index_max=df2[df2['filename']==i].index[-1]
    for ind in range(index_min,index_max):
        if (df2['object'][ind] in keywords and df2['probability'][ind]>0.70):
            count=count+1
            break
    
    
    
    

In [32]:
count

862

In [20]:
result1=1036/3820
print("Core post: {0:.2f}%".format(result1*100))

Core post: 27.12%


In [30]:
result2=count/len(num_images)
print("storiest: {0:.2f}%".format(result2*100))

storiest: 34.66%


In [267]:
df

filename                         object  probability
0             1                        product     0.834238
1             1                    sport venue     0.793123
2             1                      structure     0.776179
3             1                        product     0.679219
4             1                           play     0.661621
5             1                     recreation     0.515665
6             1                      fast food     0.500111
7             2                            red     0.965575
8             2                         finger     0.807831
9             2                        t shirt     0.714279
10            2                           hand     0.660781
11            2                           font     0.633451
12            2                         zipper     0.630276
13            2                        product     0.593414
14            2                           nail     0.572853
15            2                         button     0.560788
16            2                          label     0.549453
17            3                       footwear     0.983484
18            3                       sneakers     0.945894
19            3                           shoe     0.934355
20            3                          brown     0.810705
21            3                        product     0.773745
22            3                   outdoor shoe     0.689073
23            3                   walking shoe     0.629829
24            3                          brand     0.568119
25            3                          beige     0.519821
26            3                           font     0.505695
27            4                       footwear     0.990342
28            4                           shoe     0.958958
29            4                       sneakers     0.956939
30            4                        product     0.795203
31            4                   outdoor shoe     0.736419
32            4                  athletic shoe     0.711551
33            4                           cool     0.672368
34            4                   running shoe     0.660546
35            4                   walking shoe     0.616564
36            4            cross training shoe     0.558841
37            5                           pink     0.964053
38            5                         flower     0.683618
39            5                          petal     0.650266
40            5                        magenta     0.649774
41            5                           girl     0.551736
42            6                       footwear     0.984666
43            6                          black     0.951379
44            6                           shoe     0.933936
45            6                        product     0.757435
46            6                        product     0.743057
47            6                   outdoor shoe     0.734175
48            6  personal protective equipment     0.687874
49            6                       sneakers     0.645304
50            6                          brand     0.577470
51            6                  athletic shoe     0.558587
52            7                       footwear     0.990257
53            7                           blue     0.968321
54            7                           shoe     0.950707
55            7                  electric blue     0.914636
56            7                    cobalt blue     0.899458
57            7                     sportswear     0.834660
58            7                  athletic shoe     0.824811
59            7                       sneakers     0.807547
60            7                        product     0.797689
61            7                        product     0.782884
62            8                     photograph     0.960836
63            8                          black     0.951592
64            8                       snapshot     0.817675
65            8                    photography 

In [329]:
import re

In [332]:
word=in_feed_images_selfie['object'].unique()

In [362]:
in_feed_images_selfie


id                         object      prob
0         1                        t shirt  0.959756
1         1                       footwear  0.911549
2         1                     sportswear  0.885956
3         1                       shoulder  0.797446
4         1                           shoe  0.791966
5         1                         sleeve  0.765466
6         1                      outerwear  0.752519
7         1                        product  0.692231
8         1                     recreation  0.662025
9         1                       material  0.603908
10        2                          black  0.949924
11        2                           text  0.947646
12        2                black and white  0.916608
13        2                           font  0.884107
14        2         monochrome photography  0.745166
15        2                     monochrome  0.732394
16        2                           logo  0.681876
17        2                           area  0.672010
18        2                          night  0.668618
19        2                       darkness  0.666523
20        3                   music artist  0.864889
21        3                        product  0.720744
22        3                    performance  0.637939
23        3                     gold medal  0.631166
24        3              competition event  0.624242
25        3                        singing  0.575660
26        3                            fun  0.502311
27        4                       landmark  0.921739
28        4                       building  0.910864
29        4                          night  0.909465
30        4              metropolitan area  0.899690
31        4                   architecture  0.836497
32        4                     metropolis  0.820673
33        4                     urban area  0.807702
34        4                           city  0.800091
35        4                       downtown  0.739861
36        4                       lighting  0.732956
37        5                          black  0.950514
38        5                           text  0.931881
39        5                black and white  0.907476
40        5                           font  0.838766
41        5                     monochrome  0.752855
42        5                           logo  0.739425
43        5                     atmosphere  0.718655
44        5              automotive design  0.705190
45        5             computer wallpaper  0.692535
46        5         monochrome photography  0.672805
47        6                           text  0.932344
48        6                           font  0.904977
49        6                black and white  0.835876
50        6                           logo  0.735727
51        6                        product  0.682742
52        6                     monochrome  0.651608
53        6                          brand  0.627909
54        6                       graphics  0.563585
55        6                    advertising  0.526457
56        6                         symbol  0.509750
57        7                            arm  0.686936
58        7                          human  0.682488
59        7                          joint  0.545233
60        8                 human behavior  0.639928
61        9                          black  0.956297
62        9                black and white  0.932670
63        9         monochrome photography  0.840171
64        9                     atmosphere  0.825944
65        9                    photography  0.811374
66        9                     monochrome  0.779363
67        9                       darkness  0.711703
68        9             computer wallpaper  0.602607
69        9                           font  0.594226
70        9                          space  0.553986
71       10                       clothing  0.952292
72       10                       footwear  0.951177
73       10                          child  0.948305
74       10                       

In [344]:
b=' '.join(a)


In [360]:
re.findall('photo',b)

['photo',
 'photo',
 'photo',
 'photo',
 'photo',
 'photo',
 'photo',
 'photo',
 'photo',
 'photo',
 'photo',
 'photo',
 'photo']

In [363]:
a

['t shirt',
 'footwear',
 'sportswear',
 'shoulder',
 'shoe',
 'sleeve',
 'outerwear',
 'product',
 'recreation',
 'material',
 'black',
 'text',
 'black and white',
 'font',
 'monochrome photography',
 'monochrome',
 'logo',
 'area',
 'night',
 'darkness',
 'music artist',
 'performance',
 'gold medal',
 'competition event',
 'singing',
 'fun',
 'landmark',
 'building',
 'metropolitan area',
 'architecture',
 'metropolis',
 'urban area',
 'city',
 'downtown',
 'lighting',
 'atmosphere',
 'automotive design',
 'computer wallpaper',
 'brand',
 'graphics',
 'advertising',
 'symbol',
 'arm',
 'human',
 'joint',
 'human behavior',
 'photography',
 'space',
 'clothing',
 'child',
 'boy',
 'male',
 'jeans',
 'uniform',
 'toddler',
 'sky',
 'sneakers',
 'personal protective equipment',
 'athletic shoe',
 'outdoor shoe',
 'cool',
 'line',
 'design',
 'pattern',
 'graphic design',
 'infrastructure',
 'road',
 'street',
 'play',
 'human body',
 'art',
 'costume',
 'performing arts',
 'flyer',
 '

In [ ]:
ana.head(10)